In [1]:
!pip install requests

Defaulting to user installation because normal site-packages is not writeable


In [1]:
import requests



In [3]:
res

[{'kinopoiskId': 792753,
  'type': 'NEUTRAL',
  'date': '2010-03-04T17:00:41',
  'positiveRating': 16,
  'negativeRating': 21,
  'author': 'Виктория Бувье',
  'title': 'По-весеннему',
  'description': 'Превосходство Тима Бертона в визуальной стороне неоспоримы и редко встретишь такого режиссера, который настолько  упорно держит свой стиль и создает все новые образы, новых любимцев публики, потрясающе воплощенных на экране. Но как у каждой медали есть обратная сторона, так и у этого всегда был один минус – мрачность. Конечно, сие можно расценить и как плюс, однако иногда зрителю нужны просто красивые сказки, с прекрасными в своем положительном безумии персонажами.  «Алиса…» именно такая. По-весеннему легкая вещь, выделяющаяся из творчества Тима не только тем, что это первый его трехмерный фильм, но и своей почти детской очаровательностью.\r\n\r\nАлиса Кингсли самая что ни на есть чудачка девятнадцати лет, постоянно выпадающая из окружающей ее серьезно-артистократической обстановки в сво

In [4]:
%%time
response = requests.get('https://kinopoiskapiunofficial.tech/api/v2.2/films', params={'order': 'RATING', 'type': 'ALL', 
                                                                                          'ratingFrom': 0, 'ratingTo': 10,
                                                                                          'yearFrom': 1000, 'yearTo': 3000,
                                                                                          'keyword': 'алиса', 'page': 1},
                       headers={"X-API-KEY": "56a4f169-32e7-444b-9d6a-a75dd49a122b"})
response

CPU times: total: 0 ns
Wall time: 48.4 ms


<Response [200]>

In [13]:
%%time
response = requests.get('https://kinopoiskapiunofficial.tech/api/v2.2/films', params={'order': 'RATING', 'type': 'ALL', 
                                                                                          'ratingFrom': 0, 'ratingTo': 10,
                                                                                          'yearFrom': 1000, 'yearTo': 3000,
                                                                                          'keyword': 'а', 'page': 1},
                       headers={"X-API-KEY": "56a4f169-32e7-444b-9d6a-a75dd49a122b"})
response.json()

CPU times: total: 0 ns
Wall time: 1.6 s


{'total': 100,
 'totalPages': 5,
 'items': [{'kinopoiskId': 1252447,
   'imdbId': 'tt9257638',
   'nameRu': 'Лорды раздевалки',
   'nameEn': None,
   'nameOriginal': 'Lords of the Lockerroom',
   'countries': [{'country': 'США'}],
   'genres': [{'genre': 'спорт'}, {'genre': 'для взрослых'}],
   'ratingKinopoisk': 9.4,
   'ratingImdb': 9.3,
   'year': 1999,
   'type': 'FILM',
   'posterUrl': 'https://kinopoiskapiunofficial.tech/images/posters/kp/1252447.jpg',
   'posterUrlPreview': 'https://kinopoiskapiunofficial.tech/images/posters/kp_small/1252447.jpg'},
  {'kinopoiskId': 1043658,
   'imdbId': 'tt4202274',
   'nameRu': 'Шоу Грязного Фрэнка',
   'nameEn': None,
   'nameOriginal': 'The Filthy Frank Show',
   'countries': [{'country': 'США'},
    {'country': 'Австралия'},
    {'country': 'Япония'}],
   'genres': [{'genre': 'комедия'}, {'genre': 'короткометражка'}],
   'ratingKinopoisk': 9.3,
   'ratingImdb': 9.2,
   'year': 2011,
   'type': 'TV_SERIES',
   'posterUrl': 'https://kinopoisk

In [2]:
def perform_request(page):
    
    keyword = 'алиса'
    
    return requests.get('https://kinopoiskapiunofficial.tech/api/v2.2/films', params={'order': 'RATING', 'type': 'ALL', 
                                                                                          'ratingFrom': 1, 'ratingTo': 10,
                                                                                          'yearFrom': 1000, 'yearTo': 3000,
                                                                                          'keyword': keyword, 
                                                                                          'page': page},
                       headers={"X-API-KEY": "56a4f169-32e7-444b-9d6a-a75dd49a122b"})

In [3]:
current_page = 1

response = perform_request(current_page)

print(response)

country_distribution = dict()

while len(response.json().get('items')):
    response = response.json().get("items")
    for film in response:
        
        if film.get("countries") is None:
            raise IndexError(f'Wrong number of countries for film {film.get("nameRu")} ({film.get("kinopoiskId")}).')
            
#         if film.get("ratingKinopoisk") is None:
#             break
            
        countries = film.get("countries")
        # print(countries)
        
        countries = list(map(lambda lst: lst[0], 
                            list(map(lambda single_cntry_dict: list(single_cntry_dict.values()), countries))))
        
        print(countries)
        ratingKP = film.get("ratingKinopoisk")
        for country in countries:
            # print(country, country_distribution)
            country_distribution.setdefault(country, [])
            country_distribution[country].append(ratingKP)     
    
    else:                
        current_page += 1
        response = perform_request(current_page)


        print(response.json())
        print(f'{current_page}')
        
        continue
        
    break
    
if 'Германия (ФРГ)' in country_distribution:
    if 'Германия' in country_distribution:        
        country_distribution.get('Германия').extend(country_distribution.get('Германия (ФРГ)'))
    else:
        country_distribution['Германия'] = country_distribution.get('Германия (ФРГ)')
    del country_distribution['Германия (ФРГ)']
    
if 'СССР' in country_distribution:
    if 'Россия' in country_distribution:        
        country_distribution.get('Россия').extend(country_distribution.get('СССР'))
    else:
        country_distribution['Россия'] = country_distribution.get('СССР')
    del country_distribution['СССР']
        

<Response [200]>
['Великобритания']
['Германия (ФРГ)']
['США']
['СССР']
['СССР']
['Корея Южная']
['Швейцария', 'Великобритания', 'Германия (ФРГ)', 'Чехословакия']
['Великобритания', 'Канада']
['Россия']
['СССР']
['Япония']
['Корея Южная']
['США', 'Великобритания']
['Япония']
['США']
['Великобритания']
['США', 'Великобритания', 'Германия']
['Япония']
['Франция']
['Россия']
{'total': 100, 'totalPages': 5, 'items': [{'kinopoiskId': 1209255, 'imdbId': None, 'nameRu': 'Алиса', 'nameEn': None, 'nameOriginal': None, 'countries': [{'country': 'Россия'}], 'genres': [{'genre': 'короткометражка'}], 'ratingKinopoisk': 6.7, 'ratingImdb': None, 'year': 2018, 'type': 'FILM', 'posterUrl': 'https://kinopoiskapiunofficial.tech/images/posters/kp/1209255.jpg', 'posterUrlPreview': 'https://kinopoiskapiunofficial.tech/images/posters/kp_small/1209255.jpg'}, {'kinopoiskId': 103466, 'imdbId': 'tt0407851', 'nameRu': 'Хана и Алиса', 'nameEn': None, 'nameOriginal': 'Hana to Arisu', 'countries': [{'country': 'Япон

{'total': 100, 'totalPages': 5, 'items': [{'kinopoiskId': 305798, 'imdbId': 'tt0898889', 'nameRu': 'Алиса в стране чудес', 'nameEn': None, 'nameOriginal': 'Alice in Wonderland', 'countries': [{'country': 'США'}, {'country': 'Канада'}, {'country': 'Япония'}], 'genres': [{'genre': 'мультфильм'}, {'genre': 'семейный'}], 'ratingKinopoisk': 5.6, 'ratingImdb': 4.8, 'year': 1995, 'type': 'FILM', 'posterUrl': 'https://kinopoiskapiunofficial.tech/images/posters/kp/305798.jpg', 'posterUrlPreview': 'https://kinopoiskapiunofficial.tech/images/posters/kp_small/305798.jpg'}, {'kinopoiskId': 20018, 'imdbId': 'tt0014656', 'nameRu': 'Алиса попадает в неприятности', 'nameEn': None, 'nameOriginal': 'Alice Gets in Dutch', 'countries': [{'country': 'США'}], 'genres': [{'genre': 'комедия'}, {'genre': 'мультфильм'}, {'genre': 'короткометражка'}], 'ratingKinopoisk': 5.6, 'ratingImdb': 5.6, 'year': 1924, 'type': 'FILM', 'posterUrl': 'https://kinopoiskapiunofficial.tech/images/posters/kp/20018.jpg', 'posterUrlP

{'total': 100, 'totalPages': 5, 'items': [{'kinopoiskId': 18465, 'imdbId': 'tt0032192', 'nameRu': 'Алиса в Киномире', 'nameEn': None, 'nameOriginal': 'Alice in Movieland', 'countries': [{'country': 'США'}], 'genres': [{'genre': 'драма'}, {'genre': 'музыка'}, {'genre': 'короткометражка'}], 'ratingKinopoisk': None, 'ratingImdb': 5.8, 'year': 1940, 'type': 'FILM', 'posterUrl': 'https://kinopoiskapiunofficial.tech/images/posters/kp/18465.jpg', 'posterUrlPreview': 'https://kinopoiskapiunofficial.tech/images/posters/kp_small/18465.jpg'}, {'kinopoiskId': 19953, 'imdbId': 'tt0015556', 'nameRu': 'Алиса выбирает чемпиона', 'nameEn': None, 'nameOriginal': 'Alice Picks the Champ', 'countries': [{'country': 'США'}], 'genres': [{'genre': 'комедия'}, {'genre': 'мультфильм'}, {'genre': 'короткометражка'}], 'ratingKinopoisk': None, 'ratingImdb': 4.6, 'year': 1925, 'type': 'FILM', 'posterUrl': 'https://kinopoiskapiunofficial.tech/images/posters/kp/19953.jpg', 'posterUrlPreview': 'https://kinopoiskapiuno

{'total': 100, 'totalPages': 5, 'items': []}
6


In [47]:
current_page

4

In [246]:
country_distribution

{'Великобритания': [8.1,
  7.6,
  7.6,
  7.1,
  7.0,
  7.0,
  6.4,
  6.3,
  6.1,
  5.2,
  3.1,
  None,
  None,
  None],
 'США': [7.9,
  7.1,
  7.1,
  7.0,
  6.7,
  6.7,
  6.7,
  6.7,
  6.5,
  6.3,
  6.0,
  6.0,
  5.7,
  5.7,
  5.6,
  5.6,
  5.6,
  5.5,
  5.4,
  5.4,
  5.3,
  5.1,
  5.1,
  5.1,
  4.7,
  4.7,
  4.0,
  2.8,
  None,
  None,
  None,
  None,
  None,
  None,
  None,
  None,
  None,
  None],
 'Швейцария': [7.6],
 'Чехословакия': [7.6],
 'Корея Южная': [7.6, 7.2, 6.0, None],
 'Канада': [7.6, 5.6],
 'Россия': [7.5,
  6.8,
  6.7,
  6.0,
  5.8,
  5.4,
  5.4,
  4.8,
  3.8,
  None,
  None,
  7.8,
  7.8,
  7.3],
 'Япония': [7.2, 7.1, 6.9, 6.7, 5.6, 5.5, None, None, None, None, None],
 'Германия': [7.0, None, None, 8.0, 7.6, None],
 'Франция': [6.8, 6.7, 6.2, 6.2, 5.4, None],
 'Испания': [6.3, 6.2, 4.9, None],
 'Бахрейн': [6.3],
 'Бельгия': [6.2, None, None, None],
 'Австралия': [5.8, None, None, None, None],
 'Италия': [4.7],
 'Украина': [3.7],
 'Нидерланды': [None],
 'Бразилия': [No

In [46]:
response

[{'kinopoiskId': 930796,
  'imdbId': None,
  'nameRu': 'Алиса знает, что делать! Зеленая месть',
  'nameEn': None,
  'nameOriginal': None,
  'countries': [{'country': 'Россия'}],
  'genres': [{'genre': 'фантастика'},
   {'genre': 'приключения'},
   {'genre': 'мультфильм'},
   {'genre': 'семейный'}],
  'ratingKinopoisk': 3.8,
  'ratingImdb': None,
  'year': 2015,
  'type': 'FILM',
  'posterUrl': 'https://kinopoiskapiunofficial.tech/images/posters/kp/930796.jpg',
  'posterUrlPreview': 'https://kinopoiskapiunofficial.tech/images/posters/kp_small/930796.jpg'},
 {'kinopoiskId': 869534,
  'imdbId': 'tt12313114',
  'nameRu': 'Алиса в стране чудес',
  'nameEn': None,
  'nameOriginal': None,
  'countries': [{'country': 'Украина'}],
  'genres': [{'genre': 'фэнтези'}, {'genre': 'комедия'}, {'genre': 'мюзикл'}],
  'ratingKinopoisk': 3.7,
  'ratingImdb': None,
  'year': 2014,
  'type': 'FILM',
  'posterUrl': 'https://kinopoiskapiunofficial.tech/images/posters/kp/869534.jpg',
  'posterUrlPreview': '

In [52]:
!pip install folium

Defaulting to user installation because normal site-packages is not writeable


In [4]:

# import the folium, pandas libraries
import folium
import pandas as pd
 
# initialize the map and store it in a m object
m = folium.Map(location = [40, -95],
               zoom_start = 10)
 
# show the map
m.save('my_map.html')
# m.show_in_browser()
m

In [3]:
folium.Map()

In [13]:
folium.Map(
    location = [64.6863136, 97.7453061],    # широта и долгота России
    zoom_start = 4,
    tiles = 'cartodb positron'
)

In [49]:
import pandas as pd

url = (
    "https://raw.githubusercontent.com/python-visualization/folium/master/examples/data"
)
state_geo = f"{url}/us-states.json"
state_unemployment = f"{url}/US_Unemployment_Oct2012.csv"
state_data = pd.read_csv(state_unemployment)

m = folium.Map(location=[48, -102], zoom_start=1)

scheme = {
    'type': 'FeatureCollection',
    'features': [
        {  
            'type': 'Feature',
            'id': 'RF',
            'properties': {'name': 'Russia'},
            'geometry': {'type': 'MultiPolygon',
                         'coordinates': [[[1, 30], [-140, 80], [-40, -150]]],
            
                       }
        }
    ]
    
}

folium.Choropleth(
    geo_data=state_geo

).add_to(m)

folium.LayerControl().add_to(m)

m

In [25]:
state_geo

'https://raw.githubusercontent.com/python-visualization/folium/master/examples/data/us-states.json'

In [44]:
import requests

response = requests.get("https://raw.githubusercontent.com/python-visualization/folium/master/examples/data/us-states.json")

In [28]:
response.json()

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'id': 'AL',
   'properties': {'name': 'Alabama'},
   'geometry': {'type': 'Polygon',
    'coordinates': [[[-87.359296, 35.00118],
      [-85.606675, 34.984749],
      [-85.431413, 34.124869],
      [-85.184951, 32.859696],
      [-85.069935, 32.580372],
      [-84.960397, 32.421541],
      [-85.004212, 32.322956],
      [-84.889196, 32.262709],
      [-85.058981, 32.13674],
      [-85.053504, 32.01077],
      [-85.141136, 31.840985],
      [-85.042551, 31.539753],
      [-85.113751, 31.27686],
      [-85.004212, 31.003013],
      [-85.497137, 30.997536],
      [-87.600282, 30.997536],
      [-87.633143, 30.86609],
      [-87.408589, 30.674397],
      [-87.446927, 30.510088],
      [-87.37025, 30.427934],
      [-87.518128, 30.280057],
      [-87.655051, 30.247195],
      [-87.90699, 30.411504],
      [-87.934375, 30.657966],
      [-88.011052, 30.685351],
      [-88.10416, 30.499135],
      [-88.137022, 30.318396],
    

In [46]:
import requests

response = requests.get("https://raw.githubusercontent.com/georgique/world-geojson/main/countries/barbados.json")

In [47]:
response.json()

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'properties': {},
   'geometry': {'type': 'Polygon',
    'coordinates': [[[-59.61181640625, 13.336175186494927],
      [-59.62623596191406, 13.33216637904759],
      [-59.64202880859375, 13.325484885597936],
      [-59.65164184570312, 13.30343464825758],
      [-59.64820861816406, 13.27135799433639],
      [-59.64752197265625, 13.257323125615741],
      [-59.640655517578125, 13.21120285795736],
      [-59.64271545410156, 13.148358327567177],
      [-59.63310241699219, 13.119604924382594],
      [-59.632415771484375, 13.109573875806992],
      [-59.626922607421875, 13.093523347481069],
      [-59.61662292480469, 13.091516957879143],
      [-59.61456298828124, 13.078140609755359],
      [-59.56443786621094, 13.062756912561527],
      [-59.54246520996093, 13.059412503703712],
      [-59.53422546386719, 13.042689780383594],
      [-59.51225280761718, 13.04536549213488],
      [-59.497146606445305, 13.056736944013103],
     

In [51]:
!pip install googletrans

Defaulting to user installation because normal site-packages is not writeable
  Created wheel for googletrans: filename=googletrans-3.0.0-py3-none-any.whl size=15749 sha256=b4f7ba84d61fe3753b15c6ee1c95a36c2fbc566ba9c241db7582588c32cb2ed7
  Stored in directory: c:\users\yaroslav pristalov\appdata\local\pip\cache\wheels\27\f3\32\d4859d40071f07a5df0ab6fdc0076e78a8a786625dde2b4b2f
Successfully built googletrans


  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
spyder 5.1.5 requires pyqt5<5.13, which is not installed.
spyder 5.1.5 requires pyqtwebengine<5.13, which is not installed.
conda-repo-cli 1.0.4 requires pathlib, which is not installed.
anaconda-project 0.10.2 requires ruamel-yaml, which is not installed.


In [62]:
from googletrans import Translator

translator = Translator()
translator.token_acquirer.acquire()

TypeError: acquire() missing 1 required positional argument: 'text'

In [56]:
from googletrans import LANGUAGES
LANGUAGES

{'af': 'afrikaans',
 'sq': 'albanian',
 'am': 'amharic',
 'ar': 'arabic',
 'hy': 'armenian',
 'az': 'azerbaijani',
 'eu': 'basque',
 'be': 'belarusian',
 'bn': 'bengali',
 'bs': 'bosnian',
 'bg': 'bulgarian',
 'ca': 'catalan',
 'ceb': 'cebuano',
 'ny': 'chichewa',
 'zh-cn': 'chinese (simplified)',
 'zh-tw': 'chinese (traditional)',
 'co': 'corsican',
 'hr': 'croatian',
 'cs': 'czech',
 'da': 'danish',
 'nl': 'dutch',
 'en': 'english',
 'eo': 'esperanto',
 'et': 'estonian',
 'tl': 'filipino',
 'fi': 'finnish',
 'fr': 'french',
 'fy': 'frisian',
 'gl': 'galician',
 'ka': 'georgian',
 'de': 'german',
 'el': 'greek',
 'gu': 'gujarati',
 'ht': 'haitian creole',
 'ha': 'hausa',
 'haw': 'hawaiian',
 'iw': 'hebrew',
 'he': 'hebrew',
 'hi': 'hindi',
 'hmn': 'hmong',
 'hu': 'hungarian',
 'is': 'icelandic',
 'ig': 'igbo',
 'id': 'indonesian',
 'ga': 'irish',
 'it': 'italian',
 'ja': 'japanese',
 'jw': 'javanese',
 'kn': 'kannada',
 'kk': 'kazakh',
 'km': 'khmer',
 'ko': 'korean',
 'ku': 'kurdish 

In [67]:
!pip install translate-api

Defaulting to user installation because normal site-packages is not writeable


In [135]:

country_distribution

{'Великобритания': [8.1,
  7.6,
  7.6,
  7.1,
  7.0,
  7.0,
  6.4,
  6.3,
  6.1,
  5.2,
  3.1,
  None,
  None,
  None],
 'США': [7.9,
  7.1,
  7.1,
  7.0,
  6.7,
  6.7,
  6.7,
  6.7,
  6.5,
  6.3,
  6.0,
  6.0,
  5.7,
  5.7,
  5.6,
  5.6,
  5.6,
  5.5,
  5.4,
  5.4,
  5.3,
  5.1,
  5.1,
  5.1,
  4.7,
  4.7,
  4.0,
  2.8,
  None,
  None,
  None,
  None,
  None,
  None,
  None,
  None,
  None,
  None,
  None,
  None,
  None,
  None,
  None,
  None],
 'СССР': [7.8, 7.8, 7.3, None],
 'Швейцария': [7.6],
 'Чехословакия': [7.6],
 'Корея Южная': [7.6, 7.2, 6.0, None, None, None],
 'Канада': [7.6, 5.6],
 'Россия': [7.5,
  6.8,
  6.7,
  6.0,
  5.8,
  5.4,
  5.4,
  4.8,
  3.8,
  None,
  None,
  None,
  None],
 'Япония': [7.2, 7.1, 6.9, 6.7, 5.6, 5.5, None, None],
 'Германия': [7.0, None, None, 8.0, 7.6],
 'Франция': [6.8, 6.7, 6.2, 6.2, 5.4, None],
 'Испания': [6.3, 6.2, 4.9, None],
 'Бахрейн': [6.3],
 'Бельгия': [6.2, None, None],
 'Австралия': [5.8, None],
 'Италия': [4.7, None],
 'Украина': [

In [178]:
coordinates

[{'type': 'Feature',
  'properties': {'country_name': 'russia'},
  'geometry': {'type': 'Polygon',
   'coordinates': [[[53.6297607421875, 51.382066781130575],
     [53.59130859375, 51.36492148825955],
     [53.61602783203125, 51.34605424944661],
     [53.6077880859375, 51.31516382328001],
     [53.6077880859375, 51.291123547147215],
     [53.6517333984375, 51.26878915771344],
     [53.6737060546875, 51.23096775701038],
     [53.70391845703125, 51.227527905265006],
     [53.74237060546875, 51.20860412431918],
     [53.800048828125, 51.217206807233396],
     [53.8385009765625, 51.19999983412068],
     [53.9208984375, 51.19655766797793],
     [54.052734375, 51.155231611562265],
     [54.03076171874994, 51.13972478986592],
     [54.15435791015619, 51.103521942404186],
     [54.13787841796875, 51.06211251399775],
     [54.18731689453119, 51.034485632974125],
     [54.16534423828125, 51.012026657382386],
     [54.195556640625, 50.9930144097952],
     [54.19281005859375, 50.970535344046034],


In [6]:
import translators as ts

# wyw_text = 'Великобритания'
# ts.translate_text(wyw_text, from_language='ru', to_language='en', translator='google')

In [8]:
%%time

import sys

replaces = {
    'ussr': 'russia',
    'united_states': 'usa'
}

coordinates = []

for country in country_distribution:

    
    translated_country = ts.bing(country, from_language='ru', to_language='en')
    translated_country = translated_country.lower().replace(' ', '_')
    translated_country = replaces.get(translated_country, translated_country)
    
    print(country, translated_country)
    
        
    if country == 'Чехословакия':
        print("Чехословакия")
        czech_response = requests.get(f'https://raw.githubusercontent.com/georgique/world-geojson/main/countries/czech.json')
        slovakia_response = requests.get(f'https://raw.githubusercontent.com/georgique/world-geojson/main/countries/slovakia.json')
        response = czech_response.json()
        response.get('features').extend(slovakia_response.json().get('features'))
    else:
        response = requests.get(f'https://raw.githubusercontent.com/georgique/world-geojson/main/countries/{translated_country}.json')
        print(response, end='\n\n')
        if response.status_code != 200:
            print("No response from coordinates server", file=sys.stdout)
            continue
        response = response.json()
    
    features = response.get('features')
    
    for feature in features:
        feature.get('properties')['country_name'] = country
        if country == 'Россия':
            _russia_coordinates_list_ptr = feature.get('geometry').get('coordinates')[0]
            feature.get('geometry').get('coordinates')[0] = list(map(lambda lst: [lst[0] + 360, lst[1]] if lst[0] < 0 else lst, 
                                                    _russia_coordinates_list_ptr))

    coordinates.extend(features)
    

Великобритания united_kingdom
<Response [200]>

США usa
<Response [200]>

Корея Южная south_korea
<Response [200]>

Швейцария switzerland
<Response [200]>

Чехословакия czechoslovakia
Чехословакия
Канада canada
<Response [200]>

Россия russia
<Response [200]>

Япония japan
<Response [200]>

Германия germany
<Response [200]>

Франция france
<Response [200]>

Испания spain
<Response [200]>

Бахрейн bahrain
<Response [200]>

Бельгия belgium
<Response [200]>

Австралия australia
<Response [200]>

Италия italy
<Response [200]>

Украина ukraine
<Response [200]>

Тайвань taiwan
<Response [404]>

No response from coordinates server
CPU times: total: 328 ms
Wall time: 24.9 s


In [192]:
pprint(coordinates)

[{'geometry': {'coordinates': [[[-1.9061279296875, 57.68800141680898],
                                [-2.0928955078125, 57.72615266321315],
                                [-2.17254638671875, 57.707082064445736],
                                [-2.29888916015625, 57.717352096870876],
                                [-2.4169921874999996, 57.69387345579735],
                                [-2.60101318359375, 57.70854939030575],
                                [-2.86468505859375, 57.723219378882284],
                                [-3.0377197265625, 57.68359676303728],
                                [-3.1256103515625, 57.70267973009526],
                                [-3.2958984375, 57.745213216291866],
                                [-3.5101318359375, 57.723219378882284],
                                [-3.5513305664062496, 57.68359676303728],
                                [-3.74908447265625, 57.66597279400861],
                                [-3.86993408203125, 57.610107020

 {'geometry': {'coordinates': [[[-63.197479248046875, 18.276302250871954],
                                [-63.20228576660156, 18.265869811558165],
                                [-63.170700073242195, 18.256740912815104],
                                [-63.13911437988282, 18.26000128888889],
                                [-63.1329345703125, 18.267173900767578],
                                [-63.14392089843749, 18.27369419984127],
                                [-63.170700073242195, 18.276302250871954],
                                [-63.197479248046875, 18.276302250871954]]],
               'type': 'Polygon'},
  'id': '43',
  'properties': {'country_name': 'united_kingdom'},
  'type': 'Feature'},
 {'geometry': {'coordinates': [[[-63.419437408447266, 18.597768236342965],
                                [-63.429737091064446, 18.5951650586388],
                                [-63.431968688964844, 18.587843408019502],
                                [-63.430767059326165, 18.57

                                [-100.69931030273438, 29.114975171051782],
                                [-100.67184448242188, 29.093377063767363],
                                [-100.65948486328125, 29.028555562818426],
                                [-100.64300537109375, 28.999732931519468],
                                [-100.6512451171875, 28.948072282131655],
                                [-100.634765625, 28.93124697186731],
                                [-100.63339233398438, 28.9072060763367],
                                [-100.61691284179688, 28.9072060763367],
                                [-100.58807373046875, 28.88796934830343],
                                [-100.60043334960938, 28.88075465630399],
                                [-100.5743408203125, 28.856702064061942],
                                [-100.57571411132812, 28.82903470307381],
                                [-100.55099487304688, 28.831440852615142],
                                [-100.53

                                [-68.24020385742188, 44.15831713326841]]],
               'type': 'Polygon'},
  'id': '110',
  'properties': {'country_name': 'usa'},
  'type': 'Feature'},
 {'geometry': {'coordinates': [[[-68.90625, 43.87290072352132],
                                [-68.90419006347656, 43.86300013486109],
                                [-68.91242980957031, 43.84888895466102],
                                [-68.89904022216797, 43.84443209873525],
                                [-68.8901138305664, 43.843194024103035],
                                [-68.89354705810547, 43.84022254015262],
                                [-68.90316009521484, 43.823629034783124],
                                [-68.90178680419922, 43.819418008560156],
                                [-68.88839721679688, 43.81768397025563],
                                [-68.87672424316405, 43.81520668532002],
                                [-68.873291015625, 43.824372126225406],
                 

                                [-120.29685974121094, 34.024209560512354],
                                [-120.31951904296874, 34.04867701532947],
                                [-120.3277587890625, 34.06517433677496],
                                [-120.34011840820312, 34.063467866218254],
                                [-120.34973144531249, 34.06801837800197],
                                [-120.37307739257812, 34.08451193447477]]],
               'type': 'Polygon'},
  'id': '209',
  'properties': {'country_name': 'usa'},
  'type': 'Feature'},
 {'geometry': {'coordinates': [[[-123.01563262939453, 37.70202228211617],
                                [-123.0164909362793, 37.69957750311584],
                                [-123.01340103149413, 37.694687703235914],
                                [-123.00310134887695, 37.69332936825816],
                                [-122.99726486206055, 37.69455187085791],
                                [-122.99932479858398, 37.7010715443079

...

 {'geometry': {'coordinates': [[[123.56529235839844, -34.33464798879872],
                                [123.55602264404291, -34.33436448702629],
                                [123.54984283447266, -34.34740457681594],
                                [123.53919982910156, -34.35590789074157],
                                [123.52993011474604, -34.35675817469359],
                                [123.52821350097656, -34.36469374226994],
                                [123.53096008300781, -34.3799959288835],
                                [123.541259765625, -34.382829360365264],
                                [123.55293273925781, -34.36979478173757],
                                [123.56563568115234, -34.359308974793564],
                                [123.5628890991211, -34.34627073645812],
                                [123.56529235839844, -34.33464798879872]]],
               'type': 'Polygon'},
  'id': '1963',
  'properties': {'country_name': 'australia'},
  'type': 'Fea

                                [124.64229583740229, -15.160287483658962]]],
               'type': 'Polygon'},
  'id': '2096',
  'properties': {'country_name': 'australia'},
  'type': 'Feature'},
 {'geometry': {'coordinates': [[[124.66787338256836, -15.147529183275303],
                                [124.66392517089838, -15.149517540435015],
                                [124.6644401550293, -15.153162813371107],
                                [124.66718673706055, -15.157967849913916],
                                [124.6731948852539, -15.158299227720924],
                                [124.67697143554682, -15.160287483658962],
                                [124.67817306518555, -15.156310953090907],
                                [124.67422485351557, -15.15067740681745],
                                [124.6699333190918, -15.152002960612576],
                                [124.66787338256836, -15.147529183275303]]],
               'type': 'Polygon'},
  'id': '2097',
  'p

 {'geometry': {'coordinates': [[[13.056221008300781, 40.97458450202252],
                                [13.053474426269531, 40.974973314165055],
                                [13.050899505615234, 40.972640406936456],
                                [13.0462646484375, 40.97147392238617],
                                [13.042144775390511, 40.96888166065838],
                                [13.04574966430664, 40.96408570797472],
                                [13.050899505615234, 40.96330795307353],
                                [13.05999755859375, 40.96304869940295],
                                [13.064804077148438, 40.96551156815455],
                                [13.065147399902344, 40.9713443117186],
                                [13.056221008300781, 40.97458450202252]]],
               'type': 'Polygon'},
  'id': '2160',
  'properties': {'country_name': 'italy'},
  'type': 'Feature'},
 {'geometry': {'coordinates': [[[12.853660583496094, 40.95189982816191],
         

                                [22.429962158203125, 48.92430395329745],
                                [22.424468994140625, 48.888197770982316],
                                [22.388763427734375, 48.87284474327183],
                                [22.375030517578125, 48.84212454876025],
                                [22.386016845703125, 48.80053192168114],
                                [22.350311279296875, 48.76976735954908],
                                [22.34344482421875, 48.75256718365392],
                                [22.361297607421875, 48.73717255965176],
                                [22.35305786132812, 48.7190551996152],
                                [22.335205078125, 48.68370757165364],
                                [22.300872802734375, 48.67464007858367],
                                [22.251434326171875, 48.646520476743575],
                                [22.237701416015625, 48.62564740882851],
                                [22.212982177734375, 48

               'type': 'Polygon'},
  'id': '2220',
  'properties': {'country_name': 'portugal'},
  'type': 'Feature'},
 {'geometry': {'coordinates': [[[-25.75469970703125, 37.92903406232562],
                                [-25.82611083984375, 37.91820111976663],
                                [-25.8837890625, 37.88786039168385],
                                [-25.87554931640625, 37.8271414168374],
                                [-25.8013916015625, 37.759858513184625],
                                [-25.70526123046875, 37.70555348721583],
                                [-25.63385009765625, 37.72510788462094],
                                [-25.53497314453125, 37.688167468408025],
                                [-25.41412353515625, 37.67077737288316],
                                [-25.3289794921875, 37.69251435532741],
                                [-25.213623046875, 37.714244967649265],
                                [-25.13671875, 37.73379707124429],
                 

In [11]:
df_dict = {}

for country in country_distribution:
    df_dict[country] = len(country_distribution[country])
    
print(df_dict)

stat_data = pd.DataFrame(data={'Countries': df_dict.keys(), 'Metrics': df_dict.values()})
stat_data

{'Великобритания': 15, 'США': 48, 'Корея Южная': 4, 'Швейцария': 1, 'Чехословакия': 1, 'Канада': 3, 'Россия': 15, 'Япония': 9, 'Германия': 4, 'Франция': 8, 'Испания': 3, 'Бахрейн': 1, 'Бельгия': 1, 'Австралия': 1, 'Италия': 1, 'Украина': 1, 'Тайвань': 1}


Countries  Metrics
0   Великобритания       15
1              США       48
2      Корея Южная        4
3        Швейцария        1
4     Чехословакия        1
5           Канада        3
6           Россия       15
7           Япония        9
8         Германия        4
9          Франция        8
10         Испания        3
11         Бахрейн        1
12         Бельгия        1
13       Австралия        1
14          Италия        1
15         Украина        1
16         Тайвань        1

In [10]:
import pandas as pd

url = (
    "https://raw.githubusercontent.com/python-visualization/folium/master/examples/data"
)
state_geo = f"{url}/us-states.json"
state_unemployment = f"{url}/US_Unemployment_Oct2012.csv"
state_data = pd.read_csv(state_unemployment)

m = folium.Map(location=[60, 100], zoom_start=1, width='100%')

scheme = {
    'type': 'FeatureCollection',
    'features': coordinates    
}

folium.Choropleth(
    geo_data=scheme,
    name="choropleth",
    data=stat_data,
    columns=["Countries", "Metrics"],
    key_on="feature.properties.country_name",
    fill_color="BuPu",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Number of films released",

).add_to(m)

folium.LayerControl().add_to(m)

m

NameError: name 'folium' is not defined

In [227]:
requests.get('https://raw.githubusercontent.com/python-visualization/folium/master/examples/data/us-states.json').json()

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'id': 'AL',
   'properties': {'name': 'Alabama'},
   'geometry': {'type': 'Polygon',
    'coordinates': [[[-87.359296, 35.00118],
      [-85.606675, 34.984749],
      [-85.431413, 34.124869],
      [-85.184951, 32.859696],
      [-85.069935, 32.580372],
      [-84.960397, 32.421541],
      [-85.004212, 32.322956],
      [-84.889196, 32.262709],
      [-85.058981, 32.13674],
      [-85.053504, 32.01077],
      [-85.141136, 31.840985],
      [-85.042551, 31.539753],
      [-85.113751, 31.27686],
      [-85.004212, 31.003013],
      [-85.497137, 30.997536],
      [-87.600282, 30.997536],
      [-87.633143, 30.86609],
      [-87.408589, 30.674397],
      [-87.446927, 30.510088],
      [-87.37025, 30.427934],
      [-87.518128, 30.280057],
      [-87.655051, 30.247195],
      [-87.90699, 30.411504],
      [-87.934375, 30.657966],
      [-88.011052, 30.685351],
      [-88.10416, 30.499135],
      [-88.137022, 30.318396],
    

In [233]:
scheme

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'properties': {'country_name': 'Великобритания'},
   'geometry': {'type': 'Polygon',
    'coordinates': [[[-1.9061279296875, 57.68800141680898],
      [-2.0928955078125, 57.72615266321315],
      [-2.17254638671875, 57.707082064445736],
      [-2.29888916015625, 57.717352096870876],
      [-2.4169921874999996, 57.69387345579735],
      [-2.60101318359375, 57.70854939030575],
      [-2.86468505859375, 57.723219378882284],
      [-3.0377197265625, 57.68359676303728],
      [-3.1256103515625, 57.70267973009526],
      [-3.2958984375, 57.745213216291866],
      [-3.5101318359375, 57.723219378882284],
      [-3.5513305664062496, 57.68359676303728],
      [-3.74908447265625, 57.66597279400861],
      [-3.86993408203125, 57.61010702068388],
      [-4.04296875, 57.61010702068388],
      [-3.779296875, 57.80526150191621],
      [-3.7298583984375004, 57.88273703534323],
      [-3.8232421874999996, 57.88127677495476],
      [-3.88

In [237]:
folium.Map(location=[48, -102], zoom_start=1)

In [1]:
from src.KinopoiskAnalyzer.requests import FiltersRequester

FiltersRequester().perform().json()

__module__
PURPLE
CYAN
DARKCYAN
BLUE
GREEN
YELLOW
RED
BOLD
ITALIC
UNDERLINE
BLINKING
CROSSED
END
__dict__
__weakref__
__doc__
__dataclass_params__
__dataclass_fields__
__init__
__repr__
__eq__
__setattr__
__delattr__
__hash__


<class 'src.KinopoiskAnalyzer.requests.FiltersRequester'>: Response's status_code = 200


{'genres': [{'id': 1, 'genre': 'триллер'},
  {'id': 2, 'genre': 'драма'},
  {'id': 3, 'genre': 'криминал'},
  {'id': 4, 'genre': 'мелодрама'},
  {'id': 5, 'genre': 'детектив'},
  {'id': 6, 'genre': 'фантастика'},
  {'id': 7, 'genre': 'приключения'},
  {'id': 8, 'genre': 'биография'},
  {'id': 9, 'genre': 'фильм-нуар'},
  {'id': 10, 'genre': 'вестерн'},
  {'id': 11, 'genre': 'боевик'},
  {'id': 12, 'genre': 'фэнтези'},
  {'id': 13, 'genre': 'комедия'},
  {'id': 14, 'genre': 'военный'},
  {'id': 15, 'genre': 'история'},
  {'id': 16, 'genre': 'музыка'},
  {'id': 17, 'genre': 'ужасы'},
  {'id': 18, 'genre': 'мультфильм'},
  {'id': 19, 'genre': 'семейный'},
  {'id': 20, 'genre': 'мюзикл'},
  {'id': 21, 'genre': 'спорт'},
  {'id': 22, 'genre': 'документальный'},
  {'id': 23, 'genre': 'короткометражка'},
  {'id': 24, 'genre': 'аниме'},
  {'id': 25, 'genre': ''},
  {'id': 26, 'genre': 'новости'},
  {'id': 27, 'genre': 'концерт'},
  {'id': 28, 'genre': 'для взрослых'},
  {'id': 29, 'genre': 'це

In [1]:
from src.kinopoisk_analyzer.service.data_syncers import sync_countries, sync_genres

In [2]:
sync_countries()
sync_genres()